# regression with neriol networks 

---
### backgroud & goal

通过对比简单神经网络与回归方程，加深对两者的理解与印象

平台基于pytorch与sklearn构建，前期数据处理流程尽量保存一致。

---

### 建立的回归方程 The type Of regression：

1. 多元回归
2. 逻辑回归
3. 多分类

----

### 数据来源包括 data source：

1. 信用卡数据
2. 汽车数据

---

### 模型过程

数据读取->EDA->数据整理（edit data）->模型建立->模型验证->模型部署

不论是回归抑或神经网络都依照这一流程

> pytorch 部署时数据处理使用 dataset，dataloader包装。
> 分类判断 

## 实验1：汽车价格数据
### overview:

In this lab you will apply regression to some realistic data. In this lab you will work with the automotive price dataset. Your goal is to construct a linear regression model to predict the price of automobiles from their characteristics. 

In this lab will learn to:

1. Use categorical data with scikit-learn. 
2. Apply transformations to features and labels to improve model performance. 
3. Compare regression models to improve model performance. 
4. Apply neorl network to the same data.

----

critial points:

1，EDA
2. Data processing 中 dumy数据处理
3. Embedding 层的使用
4. 使用sklearn pipeline



[](https://towardsdatascience.com/deep-learning-for-tabular-data-using-pytorch-1807f2858320)

In [17]:
import sys,os 
import common.util
sys.path.append(os.pardir)
print(os.getcwd())
print(os.path.abspath('.'))
print(os.pardir)
current_path = os.path.abspath('.')
print("current",current_path)
file=os.path.join(current_path,'/data/Automobile price data _Raw_.csv')
print(file)
 

c:\Users\tom\OneDrive\文档\GitHub\IRM_class\Deep Learning
c:\Users\tom\OneDrive\文档\GitHub\IRM_class\Deep Learning
..
current c:\Users\tom\OneDrive\文档\GitHub\IRM_class\Deep Learning
c:/data/Automobile price data _Raw_.csv


1.1 eda 
[参考](https://towardsdatascience.com/exploratory-data-analysis-eda-visualization-using-pandas-ca5a04271607)

In [18]:
import numpy as np 
import pandas as pd 
####################Preping Data###################### 
# 1. get data
current_path = os.getcwd()
#file=os.path.join(current_path,'/data/Automobile price data _Raw_.csv')
file='data/Automobile price data _Raw_.csv'
print(file)
auto_price_df=pd.read_csv(file)
# 2. eda base on pandas functions 基于pandas 对数据eda 
print("数据基本信息:")
print(auto_price_df.info())
print("****************************************************************")
print("数据描述信息:")
print(auto_price_df.describe())
print("****************************************************************")
head=5
print("前{}行数据：".format(head))
print(auto_price_df.head(head))
print("****************************************************************")


data/Automobile price data _Raw_.csv
数据基本信息:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 205 entries, 0 to 204
Data columns (total 26 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   symboling          205 non-null    int64  
 1   normalized-losses  205 non-null    object 
 2   make               205 non-null    object 
 3   fuel-type          205 non-null    object 
 4   aspiration         205 non-null    object 
 5   num-of-doors       205 non-null    object 
 6   body-style         205 non-null    object 
 7   drive-wheels       205 non-null    object 
 8   engine-location    205 non-null    object 
 9   wheel-base         205 non-null    float64
 10  length             205 non-null    float64
 11  width              205 non-null    float64
 12  height             205 non-null    float64
 13  curb-weight        205 non-null    int64  
 14  engine-type        205 non-null    object 
 15  num-of-cylinders   205 non-nu

对数据中Null值，缺失值进行分析，

In [19]:
import pandas as pd 
def datainfo_null(df:pd.DataFrame)->None:
    if df.isnull().values.any(): 
        null_count=df.isnull().sum()
        al_count=df.shape[0]
        print("数据框存在null行{},占比{:.2f}".format(null_count, null_count/al_count))
    else:
        print("数据框没有非空行")

def datainfo_duplicate(df:pd.DataFrame)->None:
    if auto_price_df.duplicated().values.any(): 
        null_count=auto_price_df.duplicated().sum()
        al_count=df.shape[0]
        print("数据框存在重复行{},占比{:.2f}".format(null_count, null_count/al_count))
    else:
        print("数据框没有重复行")
if __name__=="__main__":
    datainfo_null(auto_price_df)
    datainfo_duplicate(auto_price_df)
 

数据框没有非空行
数据框没有重复行


In [ ]:
!pip install pandas-profiling

数据分布分析

为了简化，可以采用 pandas-profiling 对Dataframe数据进行DEA

在以上数据基础上，再通过箱图观察，得到float的具体极端值数据。

In [24]:
import pandas_profiling as pp
pp.ProfileReport(auto_price_df)



C:\Users\tom\AppData\Local\Temp\ipykernel_22252\2118621680.py:1: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling` instead.
  import pandas_profiling as pp


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

根据数据报告，得到：
1. 部分属性出现 high cardinality 高基数

high-cardinality categorical attributes，从字面上理解，即对于某个category特征，不同值的数量非常多，这里暂且把它叫做高数量类别属性。反之，即低数量类别属性（low-cardinality）

对于低数量类别属性，通常在data science中采用的方式是将其转化为one-hot编码，即给每一个类别增加一个特征。但是当类别数量增加的时候，ont-hot编码增加的特征也在增加。所以， **one-hot编码无法适用于高数量特征属性**。

2. 部分数据出现 imbalance现象

---

单纯的依靠对数据观察无法指定下一步的数据清洗与分析计划，例如normalized-losses出现了high cardinality 现象，并存在大量的'?'字符，但该列代表含义不明确的情况下难以对其进行处理。如果normalized-losses出现问题数据过多，则直接删除该列。

---



数据观察得到，其中price作为因变量数据类型为obejct(str)对象类型，应该转换称为float浮点型

[参考](https://sparkbyexamples.com/pandas/pandas-convert-string-to-float-type-dataframe/)

但转换时，数据中出现'?'符号，不能直接通过astype转换，需要首先，找到并去除出现'?'的行。

同时其他列中也可能出现'?'或空白字符串'  '为此，自定义函数，首先进行统计，并去掉该列中无效行。
---

同时由于列名中出现'-'字符，会影响后期数据处理，将其替换为'_'

> Recode names

Notice that several of the column names contain the '-' character. Python will not correctly recognize character strings containing '-'.  Rather, such a name will be recognized as two character strings. The same problem will occur with column values containing many special characters including, '-', ',', '*', '/', '|', '>', '<', '@', '!' etc. If such characters appear in column names of values, they must be replaced with another character. 

Execute the code in the cell below to replace the '-' characters by '_':

In [20]:
def error_info(df:pd.DataFrame):
    
    #all=df.__len__
    #print(all)
    
        
    for col in df.columns:
        #if df[col].dtype == object:
            count=0
            for row in df[col]:
                if  row=='?':
                    count+=count
    print('列{}中含有非法字符数据{}行'.format(col,count))
                    
 
if __name__ == "__main__":
    error_info(auto_price_df)
    try:
        auto_price_df['price']=auto_price_df['price'].astype(float)
        #print(auto_price_df.dtypes)
        print("price数据类型转换成功")
    except Exception as e:
        print("出现异常：",e)
        print("通过异常处理程序，price数据类型转换成功")
        #print(auto_price_df.loc[auto_price_df['price']=='?'])
        auto_price_df.drop(auto_price_df[auto_price_df['price']=='?'].index, inplace=True)
        auto_price_df['price']=auto_price_df['price'].astype(float)
        print(auto_price_df.dtypes)

################################列改名################################
    auto_price_df.columns = auto_price_df.columns = [str.replace('-', '_') for str in auto_price_df.columns]
    print(type(auto_price_df.columns.name))

列price中含有非法字符数据0行
出现异常： could not convert string to float: '?'
通过异常处理程序，price数据类型转换成功
symboling              int64
normalized-losses     object
make                  object
fuel-type             object
aspiration            object
num-of-doors          object
body-style            object
drive-wheels          object
engine-location       object
wheel-base           float64
length               float64
width                float64
height               float64
curb-weight            int64
engine-type           object
num-of-cylinders      object
engine-size            int64
fuel-system           object
bore                  object
stroke                object
compression-ratio    float64
horsepower            object
peak-rpm              object
city-mpg               int64
highway-mpg            int64
price                float64
dtype: object
<class 'NoneType'>


In [21]:
auto_price_df

symboling normalized_losses         make fuel_type aspiration  \
0            3                 ?  alfa-romero       gas        std   
1            3                 ?  alfa-romero       gas        std   
2            1                 ?  alfa-romero       gas        std   
3            2               164         audi       gas        std   
4            2               164         audi       gas        std   
..         ...               ...          ...       ...        ...   
200         -1                95        volvo       gas        std   
201         -1                95        volvo       gas      turbo   
202         -1                95        volvo       gas        std   
203         -1                95        volvo    diesel      turbo   
204         -1                95        volvo       gas      turbo   

    num_of_doors   body_style drive_wheels engine_location  wheel_base  ...  \
0            two  convertible          rwd           front        88.6  ...   
1            two  convertible          rwd           front        88.6  ...   
2            two    hatchback          rwd           front        94.5  ...   
3           four        sedan          fwd           front        99.8  ...   
4           four        sedan          4wd           front        99.4  ...   
..           ...          ...          ...             ...         ...  ...   
200         four        sedan          rwd           front       109.1  ...   
201         four        sedan          rwd           front       109.1  ...   
202         four        sedan          rwd           front       109.1  ...   
203         four        sedan          rwd           front       109.1  ...   
204         four        sedan          rwd           front       109.1  ...   

     engine_size  fuel_system  bore  stroke compression_ratio horsepower  \
0            130         mpfi  3.47    2.68               9.0        111   
1            130         mpfi  3.47    2.68               9.0        111   
2            152         mpfi  2.68    3.47               9.0        154   
3            109         mpfi  3.19    3.40              10.0        102   
4            136         mpfi  3.19    3.40               8.0        115   
..           ...          ...   ...     ...               ...        ...   
200          141         mpfi  3.78    3.15               9.5        114   
201          141         mpfi  3.78    3.15               8.7        160   
202          173         mpfi  3.58    2.87               8.8        134   
203          145          idi  3.01    3.40              23.0        106   
204          141         mpfi  3.78    3.15               9.5        114   

     peak_rpm city_mpg highway_mpg    price  
0        5000       21          27  13495.0  
1        5000       21          27  16500.0  
2        5000       19          26  16500.0  
3        5500       24          30  13950.0  
4        5500       18          22  17450.0  
..        ...      ...         ...      ...  
200      5400       23          28  16845.0  
201      5300       19          25  19045.0  
202      5500       18          23  21485.0  
203      4800       26          27  22470.0  
204      5400       19          25  22625.0  

[201 rows x 26 columns]

In [ ]:
auto_price_df['']

step.数据预处理 data processing

* 基于pandas sklearn 的数据预处理
由于numpy单纯为数据向量，没有列名，故在分割数据时，可以先基于Dataframe更为直观方便，包括


1. 因变量自变量数据分割，

```python
from sklearn.model_selection import train_test_split
```

2. category数据处理

3. trani,test 数据分割

4. 对train数据的标准化

 



In [58]:
from sklearn.model_selection import train_test_split
################################因变量自变量分割，转换numpy################################
dependentVars=auto_price_df['price'].to_numpy()
print("因变量price为向量，形状为{}".format(dependentVars.shape))
#删除因变量，创建自变量DataFrame
independentVars=auto_price_df.drop('price',axis=1)
#train_data,test_data = train_test_split(auto_price_df, test_size=0.33, random_state=42)
################################实现category类型变量处理###################################
print("通过数据观察，数据集确定其中nominal 类型包括：")

因变量price为向量，形状为(205,)


symboling normalized-losses         make fuel-type aspiration  \
0            3                 ?  alfa-romero       gas        std   
1            3                 ?  alfa-romero       gas        std   
2            1                 ?  alfa-romero       gas        std   
3            2               164         audi       gas        std   
4            2               164         audi       gas        std   
..         ...               ...          ...       ...        ...   
200         -1                95        volvo       gas        std   
201         -1                95        volvo       gas      turbo   
202         -1                95        volvo       gas        std   
203         -1                95        volvo    diesel      turbo   
204         -1                95        volvo       gas      turbo   

    num-of-doors   body-style drive-wheels engine-location  wheel-base  ...  \
0            two  convertible          rwd           front        88.6  ...   
1            two  convertible          rwd           front        88.6  ...   
2            two    hatchback          rwd           front        94.5  ...   
3           four        sedan          fwd           front        99.8  ...   
4           four        sedan          4wd           front        99.4  ...   
..           ...          ...          ...             ...         ...  ...   
200         four        sedan          rwd           front       109.1  ...   
201         four        sedan          rwd           front       109.1  ...   
202         four        sedan          rwd           front       109.1  ...   
203         four        sedan          rwd           front       109.1  ...   
204         four        sedan          rwd           front       109.1  ...   

     num-of-cylinders  engine-size  fuel-system  bore stroke  \
0                four          130         mpfi  3.47   2.68   
1                four          130         mpfi  3.47   2.68   
2                 six          152         mpfi  2.68   3.47   
3                four          109         mpfi  3.19   3.40   
4                five          136         mpfi  3.19   3.40   
..                ...          ...          ...   ...    ...   
200              four          141         mpfi  3.78   3.15   
201              four          141         mpfi  3.78   3.15   
202               six          173         mpfi  3.58   2.87   
203               six          145          idi  3.01   3.40   
204              four          141         mpfi  3.78   3.15   

    compression-ratio  horsepower peak-rpm city-mpg highway-mpg  
0                 9.0         111     5000       21          27  
1                 9.0         111     5000       21          27  
2                 9.0         154     5000       19          26  
3                10.0         102     5500       24          30  
4                 8.0         115     5500       18          22  
..                ...         ...      ...      ...         ...  
200               9.5         114     5400       23          28  
201               8.7         160     5300       19          25  
202               8.8         134     5500       18          23  
203              23.0         106     4800       26          27  
204               9.5         114     5400       19          25  

[205 rows x 25 columns]

pandas.core.series.Series